In [1]:
from gensim.models import Word2Vec
import pandas as pd
import numpy as np
import tensorflow as tf
import re
import nltk
nltk.download('stopwords') 
nltk.download('wordnet')
import nltk
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer,PorterStemmer
from nltk.corpus import stopwords
import re
from gensim.models import Word2Vec
from sklearn.decomposition import PCA
from matplotlib import pyplot
from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split
from tensorflow.python.keras.preprocessing.text import Tokenizer
from tensorflow.python.keras.preprocessing.sequence import pad_sequences
import os
stop = stopwords.words('english')

INFO:tensorflow:Enabling eager execution
INFO:tensorflow:Enabling v2 tensorshape
INFO:tensorflow:Enabling resource variables
INFO:tensorflow:Enabling tensor equality
INFO:tensorflow:Enabling control flow v2


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Chike\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Chike\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [2]:
embeddings_index={}
f=open(os.path.join('','C:\\Users\\Chike\\Documents\\Projects\\twitter-disaster-prediction\\models\\glove.twitter.27B.200d.txt'),encoding='utf-8')
# word2vec=Word2Vec.load()
for line in f:
    values=line.split()
    word=values[0]
    coefs=np.asarray(values[1:])
    embeddings_index[word]=coefs
f.close()

In [3]:
embeddings_index

{'<user>': array(['0.31553', '0.53765', '0.10177', '0.032553', '0.003798',
        '0.015364', '-0.20344', '0.33294', '-0.20886', '0.10061',
        '0.30976', '0.50015', '0.32018', '0.13537', '0.0087039', '0.1911',
        '0.24668', '-0.060752', '-0.43623', '0.019302', '0.59972',
        '0.13444', '0.012801', '-0.54052', '0.27387', '-1.182', '-0.27677',
        '0.11279', '0.46596', '-0.090685', '0.24253', '0.15654',
        '-0.23618', '0.57694', '0.17563', '-0.01969', '0.018295',
        '0.37569', '-0.41984', '0.22613', '-0.20438', '-0.076249',
        '0.40356', '0.61582', '-0.10064', '0.23318', '0.22808', '0.34576',
        '-0.14627', '-0.1988', '0.033232', '-0.84885', '-0.25684',
        '0.26369', '0.29562', '0.1847', '-0.20668', '-0.013297', '0.12233',
        '-0.47751', '-0.17202', '-0.14577', '0.047446', '-0.15824',
        '0.054215', '-0.19426', '-0.081484', '0.099009', '0.10159',
        '0.043571', '0.50245', '0.13362', '0.065985', '0.032969',
        '-0.2017', '-0.

In [4]:
train_df=pd.read_csv("C:\\Users\\Chike\\Documents\\Projects\\twitter-disaster-prediction\\data\\raw\\train.csv")
train_df

id keyword location  \
0         1     NaN      NaN   
1         4     NaN      NaN   
2         5     NaN      NaN   
3         6     NaN      NaN   
4         7     NaN      NaN   
...     ...     ...      ...   
7608  10869     NaN      NaN   
7609  10870     NaN      NaN   
7610  10871     NaN      NaN   
7611  10872     NaN      NaN   
7612  10873     NaN      NaN   

                                                   text  target  
0     Our Deeds are the Reason of this #earthquake M...       1  
1                Forest fire near La Ronge Sask. Canada       1  
2     All residents asked to 'shelter in place' are ...       1  
3     13,000 people receive #wildfires evacuation or...       1  
4     Just got sent this photo from Ruby #Alaska as ...       1  
...                                                 ...     ...  
7608  Two giant cranes holding a bridge collapse int...       1  
7609  @aria_ahrary @TheTawniest The out of control w...       1  
7610  M1.94 [01:04 UTC]?5km S of Volcano Hawaii. htt...       1  
7611  Police investigating after an e-bike collided ...       1  
7612  The Latest: More Homes Razed by Northern Calif...       1  

[7613 rows x 5 columns]

In [5]:
train_df['clean_text']=train_df['text'].apply(lambda x: re.split('https:\/\/.*', str(x))[0])
train_df['clean_text']=train_df['clean_text'].apply(lambda x: re.split('http:\/\/.*', str(x))[0])
train_df['clean_text']=train_df['clean_text'].str.replace('\d+', '')
train_df['clean_text']=train_df['clean_text'].str.lower()
train_df['clean_text']=train_df['clean_text'].str.replace('\W', ' ')
train_df['clean_text']=[' '.join([w for w in x.lower().split() if w not in stop]) for x in train_df['clean_text'].tolist()]
train_df['clean_text']=train_df['clean_text'].str.replace('\d+', '')

train_df.clean_text

<ipython-input-5-b6908ce19e96>:3: FutureWarning: The default value of regex will change from True to False in a future version.
  train_df['clean_text']=train_df['clean_text'].str.replace('\d+', '')
<ipython-input-5-b6908ce19e96>:5: FutureWarning: The default value of regex will change from True to False in a future version.
  train_df['clean_text']=train_df['clean_text'].str.replace('\W', ' ')
<ipython-input-5-b6908ce19e96>:7: FutureWarning: The default value of regex will change from True to False in a future version.
  train_df['clean_text']=train_df['clean_text'].str.replace('\d+', '')


0            deeds reason earthquake may allah forgive us
1                   forest fire near la ronge sask canada
2       residents asked shelter place notified officer...
3       people receive wildfires evacuation orders cal...
4       got sent photo ruby alaska smoke wildfires pou...
                              ...                        
7608    two giant cranes holding bridge collapse nearb...
7609    aria_ahrary thetawniest control wild fires cal...
7610                                utc km volcano hawaii
7611    police investigating e bike collided car littl...
7612    latest homes razed northern california wildfir...
Name: clean_text, Length: 7613, dtype: object

In [6]:
 X_train, X_test, y_train, y_test = train_test_split(train_df.clean_text, train_df.target, test_size=0.2, random_state=42)

In [7]:
tokenizer=Tokenizer()
total_tweets = pd.concat([X_train, X_test])
tokenizer.fit_on_texts(total_tweets)

max_length=max([len(s.split()) for s in total_tweets])

vocab_size=len(tokenizer.word_index)+1

X_train_tokens=tokenizer.texts_to_sequences(X_train)
X_test_tokens=tokenizer.texts_to_sequences(X_test)

X_train_pad=pad_sequences(X_train_tokens,maxlen=max_length,padding='post')
X_test_pad=pad_sequences(X_test_tokens,maxlen=max_length,padding='post')

In [8]:
embeddings_index

{'<user>': array(['0.31553', '0.53765', '0.10177', '0.032553', '0.003798',
        '0.015364', '-0.20344', '0.33294', '-0.20886', '0.10061',
        '0.30976', '0.50015', '0.32018', '0.13537', '0.0087039', '0.1911',
        '0.24668', '-0.060752', '-0.43623', '0.019302', '0.59972',
        '0.13444', '0.012801', '-0.54052', '0.27387', '-1.182', '-0.27677',
        '0.11279', '0.46596', '-0.090685', '0.24253', '0.15654',
        '-0.23618', '0.57694', '0.17563', '-0.01969', '0.018295',
        '0.37569', '-0.41984', '0.22613', '-0.20438', '-0.076249',
        '0.40356', '0.61582', '-0.10064', '0.23318', '0.22808', '0.34576',
        '-0.14627', '-0.1988', '0.033232', '-0.84885', '-0.25684',
        '0.26369', '0.29562', '0.1847', '-0.20668', '-0.013297', '0.12233',
        '-0.47751', '-0.17202', '-0.14577', '0.047446', '-0.15824',
        '0.054215', '-0.19426', '-0.081484', '0.099009', '0.10159',
        '0.043571', '0.50245', '0.13362', '0.065985', '0.032969',
        '-0.2017', '-0.

In [9]:
len(embeddings_index[next(iter(embeddings_index))])

200

In [10]:
EMBEDDING_DIM=200

In [11]:
num_words=len(tokenizer.word_index)+1
embedding_matrix=np.zeros((num_words,EMBEDDING_DIM))

for word,i in tokenizer.word_index.items():
    if i>num_words:
        continue
    embedding_vector=embeddings_index.get(word)
    if embedding_vector is not None:
        embedding_matrix[i]=embedding_vector
print(num_words)

15604


In [12]:
from keras.models import Sequential
from keras.layers import Dense, Embedding, LSTM, GRU
from keras.layers.embeddings import Embedding
from keras.initializers import Constant

In [13]:
max_length

25

In [14]:
from tensorflow.keras.metrics import Recall
from tensorflow.keras.metrics import Precision

In [15]:
model=Sequential()
embedding_layer=Embedding(num_words
                    ,EMBEDDING_DIM
                    ,embeddings_initializer=Constant(embedding_matrix)
                    ,input_length=max_length
                    ,trainable=False)
model.add(embedding_layer)
model.add(GRU(units=32,dropout=0.2,recurrent_dropout=0.2))
model.add(Dense(1,activation="sigmoid"))
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy',Precision(),Recall()])

In [16]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 25, 200)           3120800   
_________________________________________________________________
gru (GRU)                    (None, 32)                22464     
_________________________________________________________________
dense (Dense)                (None, 1)                 33        
Total params: 3,143,297
Trainable params: 22,497
Non-trainable params: 3,120,800
_________________________________________________________________


In [17]:
model.fit(X_train_pad,y_train,batch_size=128,epochs=120,validation_data=(X_test_pad,y_test),verbose=2)

Epoch 1/120
48/48 - 34s - loss: 0.6832 - accuracy: 0.5700 - precision: 0.5356 - recall: 0.0304 - val_loss: 0.6650 - val_accuracy: 0.5752 - val_precision: 0.5641 - val_recall: 0.0070
Epoch 2/120
48/48 - 2s - loss: 0.5300 - accuracy: 0.7445 - precision: 0.7312 - recall: 0.1289 - val_loss: 0.4692 - val_accuracy: 0.7866 - val_precision: 0.7637 - val_recall: 0.2894
Epoch 3/120
48/48 - 2s - loss: 0.4561 - accuracy: 0.8018 - precision: 0.7724 - recall: 0.3776 - val_loss: 0.4489 - val_accuracy: 0.8024 - val_precision: 0.7822 - val_recall: 0.4372
Epoch 4/120
48/48 - 2s - loss: 0.4359 - accuracy: 0.8138 - precision: 0.7907 - recall: 0.4768 - val_loss: 0.4453 - val_accuracy: 0.7958 - val_precision: 0.7956 - val_recall: 0.5084
Epoch 5/120
48/48 - 2s - loss: 0.4212 - accuracy: 0.8246 - precision: 0.8002 - recall: 0.5340 - val_loss: 0.4352 - val_accuracy: 0.8083 - val_precision: 0.8051 - val_recall: 0.5532
Epoch 6/120
48/48 - 2s - loss: 0.4144 - accuracy: 0.8278 - precision: 0.8100 - recall: 0.5681 

48/48 - 2s - loss: 0.2011 - accuracy: 0.9223 - precision: 0.8732 - recall: 0.7734 - val_loss: 0.6309 - val_accuracy: 0.7794 - val_precision: 0.8734 - val_recall: 0.7742
Epoch 47/120
48/48 - 2s - loss: 0.2065 - accuracy: 0.9190 - precision: 0.8737 - recall: 0.7750 - val_loss: 0.6378 - val_accuracy: 0.7754 - val_precision: 0.8739 - val_recall: 0.7757
Epoch 48/120
48/48 - 2s - loss: 0.1994 - accuracy: 0.9246 - precision: 0.8742 - recall: 0.7767 - val_loss: 0.6193 - val_accuracy: 0.7702 - val_precision: 0.8743 - val_recall: 0.7774
Epoch 49/120
48/48 - 2s - loss: 0.1984 - accuracy: 0.9230 - precision: 0.8746 - recall: 0.7783 - val_loss: 0.6337 - val_accuracy: 0.7669 - val_precision: 0.8747 - val_recall: 0.7790
Epoch 50/120
48/48 - 2s - loss: 0.2006 - accuracy: 0.9227 - precision: 0.8748 - recall: 0.7799 - val_loss: 0.6118 - val_accuracy: 0.7873 - val_precision: 0.8751 - val_recall: 0.7805
Epoch 51/120
48/48 - 2s - loss: 0.2009 - accuracy: 0.9232 - precision: 0.8754 - recall: 0.7812 - val_lo

Epoch 92/120
48/48 - 2s - loss: 0.1306 - accuracy: 0.9511 - precision: 0.8884 - recall: 0.8233 - val_loss: 0.7901 - val_accuracy: 0.7722 - val_precision: 0.8885 - val_recall: 0.8236
Epoch 93/120
48/48 - 2s - loss: 0.1345 - accuracy: 0.9481 - precision: 0.8886 - recall: 0.8240 - val_loss: 0.8115 - val_accuracy: 0.7663 - val_precision: 0.8886 - val_recall: 0.8243
Epoch 94/120
48/48 - 2s - loss: 0.1360 - accuracy: 0.9443 - precision: 0.8887 - recall: 0.8248 - val_loss: 0.7706 - val_accuracy: 0.7853 - val_precision: 0.8888 - val_recall: 0.8250
Epoch 95/120
48/48 - 2s - loss: 0.1406 - accuracy: 0.9442 - precision: 0.8890 - recall: 0.8253 - val_loss: 0.7582 - val_accuracy: 0.7794 - val_precision: 0.8891 - val_recall: 0.8255
Epoch 96/120
48/48 - 2s - loss: 0.1328 - accuracy: 0.9489 - precision: 0.8892 - recall: 0.8259 - val_loss: 0.7733 - val_accuracy: 0.7800 - val_precision: 0.8894 - val_recall: 0.8262
Epoch 97/120
48/48 - 2s - loss: 0.1379 - accuracy: 0.9481 - precision: 0.8895 - recall: 0.

In [18]:
val_df=pd.read_csv("C:\\Users\\Chike\\Documents\\Projects\\twitter-disaster-prediction\\data\\raw\\test.csv")
val_df

id keyword location  \
0         0     NaN      NaN   
1         2     NaN      NaN   
2         3     NaN      NaN   
3         9     NaN      NaN   
4        11     NaN      NaN   
...     ...     ...      ...   
3258  10861     NaN      NaN   
3259  10865     NaN      NaN   
3260  10868     NaN      NaN   
3261  10874     NaN      NaN   
3262  10875     NaN      NaN   

                                                   text  
0                    Just happened a terrible car crash  
1     Heard about #earthquake is different cities, s...  
2     there is a forest fire at spot pond, geese are...  
3              Apocalypse lighting. #Spokane #wildfires  
4         Typhoon Soudelor kills 28 in China and Taiwan  
...                                                 ...  
3258  EARTHQUAKE SAFETY LOS ANGELES ÛÒ SAFETY FASTE...  
3259  Storm in RI worse than last hurricane. My city...  
3260  Green Line derailment in Chicago http://t.co/U...  
3261  MEG issues Hazardous Weather Outlook (HWO) htt...  
3262  #CityofCalgary has activated its Municipal Eme...  

[3263 rows x 4 columns]

In [19]:
val_df['clean_text']=val_df['text'].apply(lambda x: re.split('https:\/\/.*', str(x))[0])
val_df['clean_text']=val_df['clean_text'].apply(lambda x: re.split('http:\/\/.*', str(x))[0])
val_df['clean_text']=val_df['clean_text'].str.replace('\d+', '')
val_df['clean_text']=val_df['clean_text'].str.lower()
val_df['clean_text']=val_df['clean_text'].str.replace('\W', ' ')
val_df['clean_text']=[' '.join([w for w in x.lower().split() if w not in stop]) for x in val_df['clean_text'].tolist()]
val_df['clean_text']=val_df['clean_text'].str.replace('\d+', '')

val_df.clean_text

<ipython-input-19-99147990c7c3>:3: FutureWarning: The default value of regex will change from True to False in a future version.
  val_df['clean_text']=val_df['clean_text'].str.replace('\d+', '')
<ipython-input-19-99147990c7c3>:5: FutureWarning: The default value of regex will change from True to False in a future version.
  val_df['clean_text']=val_df['clean_text'].str.replace('\W', ' ')
<ipython-input-19-99147990c7c3>:7: FutureWarning: The default value of regex will change from True to False in a future version.
  val_df['clean_text']=val_df['clean_text'].str.replace('\d+', '')


0                             happened terrible car crash
1       heard earthquake different cities stay safe ev...
2       forest fire spot pond geese fleeing across str...
3                   apocalypse lighting spokane wildfires
4                     typhoon soudelor kills china taiwan
                              ...                        
3258    earthquake safety los angeles ûò safety fasten...
3259    storm ri worse last hurricane city amp others ...
3260                        green line derailment chicago
3261             meg issues hazardous weather outlook hwo
3262    cityofcalgary activated municipal emergency pl...
Name: clean_text, Length: 3263, dtype: object

In [46]:
def predictions(text):
    sequence=tokenizer.texts_to_sequences(text)
        # pad the sequences
    sequence = pad_sequences(sequence, maxlen=max_length,padding='post')
        # get the prediction
    prediction = model.predict(sequence)[0]
    return prediction[0]#, [np.argmax(prediction)]

In [20]:
val_tokens=tokenizer.texts_to_sequences(val_df.clean_text)

val_pad=pad_sequences(val_tokens,maxlen=max_length,padding='post')

In [21]:
val_df['predictions']=model.predict(val_pad)

In [22]:
val_df.sort_values('predictions',ascending=False)

id              keyword                  location  \
864    2834              cyclone                       NaN   
65      217  airplane%20accident                       NaN   
1600   5402         fire%20truck                New Jersey   
1216   3991          devastation                kansas USA   
1692   5723        forest%20fire                     world   
...     ...                  ...                       ...   
58      189           aftershock  In your hearts and minds   
1040   3420               derail                Cheltenham   
3201  10638               wounds             Southern Cali   
706    2295         cliff%20fall                       NaN   
2001   6741                 lava                       NaN   

                                                   text  \
864   Is that a hurricane or a typhoon? No matter wh...   
65    Horrible Accident  Man Died In Wings of Airpla...   
1600  Truck driver died in Turnpike fire most lanes ...   
1216  70 Years After Atomic Bombs Japan Still Strugg...   
1692  Damn dry desert forest fire...damn :( https://...   
...                                                 ...   
58    @JadeForMKX You should be happy I don't use Af...   
1040  Everyone starts a #UX project with the best in...   
3201  @bkanioros Lizeth and I tried over and over ag...   
706   Mega keen for hiking tomorrow! Hope i don't fa...   
2001  HE SAID THE DOMINOS LAVA CAKES WERE BETTER THA...   

                                             clean_text  predictions  
864           hurricane typhoon matter one also cyclone     0.999958  
65          horrible accident man died wings airplaneåê     0.999956  
1600  truck driver died turnpike fire lanes still cl...     0.999955  
1216  years atomic bombs japan still struggles warti...     0.999954  
1692                   damn dry desert forest fire damn     0.999953  
...                                                 ...          ...  
58    jadeformkx happy use aftershock variation coun...     0.000082  
1040  everyone starts ux project best intentions com...     0.000078  
3201  bkanioros lizeth tried fix relationship never ...     0.000076  
706   mega keen hiking tomorrow hope fall cliff haha...     0.000074  
2001    said dominos lava cakes better culinary cuisine     0.000072  

[3263 rows x 6 columns]

In [23]:
val_df['target']=np.where(val_df['predictions']>=0.5,1,0)

In [24]:
val_df.target.value_counts()

0    1936
1    1327
Name: target, dtype: int64

In [25]:
submission_df=val_df[['id','target']]
submission_df

id  target
0         0       1
1         2       1
2         3       1
3         9       1
4        11       1
...     ...     ...
3258  10861       1
3259  10865       1
3260  10868       1
3261  10874       1
3262  10875       1

[3263 rows x 2 columns]

In [27]:
submission_df.to_csv("C:\\Users\\Chike\\Documents\\Projects\\twitter-disaster-prediction\\data\\processed\\2.2_tensorflow_glove_200d.csv",index=False)

In [80]:
!pwd

/c/Users/Chike/Documents/Projects/twitter-disaster-prediction/notebooks
